# Tutorial 2

# Computing the GO terms of the training set

In this tutorial, we are using our library to compute all the go terms present into the test set presented by the organizers of the CAFA5 competition.

In [1]:
# imports
from manas_cafa.bio.protein import Protein
from Bio import SeqIO
import random

To make this tutorial faster to run, we will work with proteins of less than 500 aminoacids. 


In [2]:
proteins = []
for record in SeqIO.parse('../cafa-5-protein-function-prediction/Train/train_sequences.fasta', 'fasta'):
    if len(record.seq) <= 500:
        proteins.append(record.id)
print('Number of proteins: {}'.format(len(proteins)))

Number of proteins: 87541


As we can observe, this is actually a good number of proteins to play with. Let's compute their GO terms in a parallel fashion:

In [3]:
# Parallel loading of go_terms into a dictionary (faster)
from joblib import Parallel, delayed
import multiprocessing

def processInput(protein_id):
    protein = Protein(protein_id)
    protein.load_uniprot()
    return {protein_id : [x['id'] for x in protein.go_terms()]}

num_cores = multiprocessing.cpu_count()*2
# compute go terms for each protein, print the evolution of the process
go_terms = Parallel(n_jobs=num_cores, verbose=100)(delayed(processInput)(i) for i in proteins)


[Parallel(n_jobs=24)]: Using backend LokyBackend with 24 concurrent workers.
[Parallel(n_jobs=24)]: Done   1 tasks      | elapsed:    1.0s
[Parallel(n_jobs=24)]: Done   2 tasks      | elapsed:    1.0s
[Parallel(n_jobs=24)]: Done   3 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   4 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   5 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   6 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   7 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   8 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done   9 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  10 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  11 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  12 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  13 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  14 tasks      | elapsed:    1.1s
[Parallel(n_jobs=24)]: Done  15 tasks      | elapsed:  

In [4]:
len(go_terms)

87541

Let's make a dictionary with the go terms as keys and the proteins as values

In [5]:
go_terms_dict = {}
for protein in go_terms:
    for key in protein.keys():
        for go_term in protein[key]:
            if go_term not in go_terms_dict.keys():
                go_terms_dict[go_term] = [key]
            else:
                go_terms_dict[go_term].append(key)

How it looks like?

In [6]:
go_terms_dict

{'GO:0003677': ['P20536',
  'P04911',
  'Q9Z288',
  'Q12415',
  'Q8BUN5',
  'B4FK49',
  'Q9C670',
  'Q6QGD4',
  'P25814',
  'Q921F2',
  'Q9SF55',
  'Q966L3',
  'Q92966',
  'Q9XIB5',
  'Q9LKG8',
  'Q84TE6',
  'A0A1X9PY88',
  'P33228',
  'Q9NX58',
  'Q9LVR0',
  'Q4KLL0',
  'P59226',
  'P15308',
  'Q92ET8',
  'O75771',
  'Q8L999',
  'Q9Y535',
  'Q9CAM7',
  'Q7KQJ9',
  'Q9ZPW7',
  'O14350',
  'Q96703',
  'A0A346LU63',
  'P58012',
  'Q9FTY0',
  'Q8AYB8',
  'P04909',
  'Q9C944',
  'Q94ID6',
  'P05549',
  'Q9VLU0',
  'Q9ET58',
  'Q6FJN0',
  'Q6NPN3',
  'Q8Y7H7',
  'Q914J4',
  'Q9LET0',
  'Q9M1G6',
  'Q15327',
  'Q9H7Z7',
  'Q96H86',
  'P22809',
  'Q9QY14',
  'Q9NZC4',
  'P70512',
  'O13722',
  'P60723',
  'Q9M9B9',
  'P07041',
  'Q9BWP8',
  'P0A4T1',
  'Q15973',
  'P67430',
  'O25896',
  'Q9ESX2',
  'P0A9H1',
  'P11416',
  'O15499',
  'Q70II3',
  'Q62424',
  'Q3UPW2',
  'Q84J70',
  'Q9Y5L5',
  'P0A9E9',
  'P02313',
  'Q00729',
  'Q9P0W2',
  'P62801',
  'P9WF09',
  'Q8LSZ4',
  'Q8T940',
  'Q9S

For future tutorials, let's save this data to a file in the `data` folder


In [7]:
with open('../data/go_terms_train_set_maxlen500.tsv', 'w') as f:
    for go_term in go_terms_dict.keys():
        f.write('{}\t{}\n'.format(go_term, ','.join(go_terms_dict[go_term])))

And also, to work with go terms that have sufficient amount of proteins to train our models, let's save also only those terms with at least 75 proteins


In [8]:
with open('../data/go_terms_train_set_maxlen500_minmembers75.tsv', 'w') as f:
    for go_term in go_terms_dict.keys():
        if len(go_terms_dict[go_term]) >= 75:
            f.write('{}\t{}\n'.format(go_term, ','.join(go_terms_dict[go_term])))